## Assignment 5
In this assignment, we look at spectral estimation and study the effects of acausal filters.

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
from setupFigure import SetupFigure
from dftFast import dft_fast_coeff, dft_fast_synthesis
from seismicTrace import SeismicTrace

### Task 1: Functions for Hann window and filter transfer functions
Write a function that calculates samples of a Hann window for given sampling interval and window length.

In [ ]:
def hann_window(dt, tlen):
    """
    Calculate samples of the Hann window for given DT and TLEN.
    Number of samples is assumed to be int(tlen/dt)
    :param dt: sampling interval
    :param tlen: length of window
    """
    ns = int(tlen/dt)
    return 2*np.sin(np.pi*dt*np.arange(0, ns)/tlen)**2

Write a function that calculates samples of the boxcar lowpass filter transfer function for positive frequencies only.

In [ ]:
def boxcar_lowpass_filter(fc, df, nf):
    """
    Calculates samples of the boxcar lowpass filter transfer function (positive frequencies only)
    :param fc: corner frequency in Hz
    :param df: frequency stepping
    :param nf: number of frequencies
    """
    return np.where(df*np.arange(0, nf) > fc, 0, 1)

Write a function that calculates samples of the boxcar highpass filter transfer function for positive frequencies only.

In [ ]:
def boxcar_highpass_filter(fc, df, nf):
    """
    Calculates samples of the boxcar highpass filter transfer function (positive frequencies only)
    :param fc: corner frequency in Hz
    :param df: frequency stepping
    :param nf: number of frequencies
    """
    return np.where(df*np.arange(0, nf) < fc, 0, 1)

Write a function that calculates samples of the Hann filter transfer function for positive frequencies only.

In [ ]:
def hann_lowpass_filter(fc, df, nf):
    """
    Calculates samples of the Hann filter transfer function (positive frequencies only)
    :param fc: corner frequency in Hz
    :param df: frequency stepping
    :param nf: number of frequencies
    """
    f = df*np.arange(0, nf)
    return np.where(f < fc, np.cos(np.pi*f/fc)**2, 0)    

### Task 2: Spectral estimation and windowing
Here, we first setup a time series that consists of a superposition of different exponentially damped sine functions simulating a series of free oscillations:
\begin{align}
s(t) = \sum_{k=0}^N A_k\sin(2\pi f_k t)\,\exp(-\pi f_k t/Q_k) \,.
\end{align}
The aim is to find the frequencies by Fourier analysis.

In [ ]:
feig = np.array([0.3, 0.48, 0.64, 0.68, 0.82, 0.85, 0.93, 0.94])*1.e-3         # eigenfreqeuncies in Hz
amp =  np.array([1.0, 0.30, 2.00, 0.61, 4.00, 0.53, 3.00, 0.24])               # amplitudes
phi =  np.array([ 11,   46,  271,  123,  337,  173,   65,  221])*np.pi/180.    # phases
q =    np.array([600,  200, 2000, 1000,  600,  100,  800,  900])               # quality factors

Write code that impements the above equation using the provided frequencies, amplitudes, phases and Q values. Choose dt=100 s and allow a varaible time series length of tens of hours. Plot the resulting time series.

In [ ]:
nhour = 100
dt = 100.0
tlen = 3600*nhour
ns = int(tlen/dt)
print("Number of samples: ", ns)
t = dt*np.arange(0, ns)
seis = np.zeros(ns)
for j, f in enumerate(feig):
    seis = seis + amp[j]*np.sin(2*np.pi*f*t+phi[j])*np.exp(-np.pi*f*t/q[j])

In [ ]:
fig1, ax1 = SetupFigure(12, 5, "Time [h|", "s(t)", "Ground motion", 14)
ax1.plot(t/3600, seis, color='blue', ls='-')

Produce a second time series by multiplying the original one with a Hann window and also plot it.

In [ ]:
win = hann_window(dt, tlen)
seisw = seis*win

In [ ]:
fig2, ax2 = SetupFigure(12, 5, "Time [h|", "swin(t)", "Windowed ground motion", 14)
ax2.plot(t/3600, seisw, color='blue', ls='-')

Perform a fast Fourier analysis, calculate the associated frequencies and plot the resulting amplitude spectra of both the original and the windowed time series. Compare the results.

In [ ]:
spec = dft_fast_coeff(seis)
f = 1./tlen*np.arange(0, spec.size)
print("Number of frequencies: ", spec.size, " fmax = ", f[-1]*1000, "mHz")

In [ ]:
specw = dft_fast_coeff(seisw)

In [ ]:
fig3, ax3 = SetupFigure(12, 5, "Frequency [mHz]", "S(f)", "Amplitude spectrum of ground motion", 14)
ax3.set_xlim(0,1.2)
ax3.plot(f*1000, np.absolute(spec), color='blue', ls='-', label='boxcar')
ax3.plot(f*1000, np.absolute(specw), color='red', ls='-', label='hann')
ax3.legend()

### Task 2: Read a seismogram from file and compute spectrum
Here, we first read a recorded seismogram form a file, do a Fourier analysis and later apply diverse acausal filters. We make use of the class "SeismicTrace" that defines a data structure for a seismic trace and also some useful functions related to traces. You may want to look at the provided code in "seismicTrace.py".

In [ ]:
seisfile = "CH.PANIX.HHZ"
with open(seisfile, 'r') as fd:
    seistrace = SeismicTrace.readFromAscii(fd)
t = seistrace.tanf+seistrace.dt*np.arange(0, seistrace.nsamp)
seistrace.printInfo()

In [ ]:
fig4, ax4 = SetupFigure(12, 5, "Time [s]", "s(t)", "Unfiltered seismic data", 14)
ax4.plot(t, seistrace.vals, color='blue', ls='-')

Perform a fast Fourier analysis, calculate the associated frequencies and plot the resulting amplitude spectrum.

In [ ]:
spec = dft_fast_coeff(seistrace.vals)
f = 1./seistrace.tlen*np.arange(0, spec.size)
print("Number of frequencies: ", spec.size, " fmax = ", f[-1], "Hz")

In [ ]:
fig5, ax5 = SetupFigure(12, 5, "Frequency [Hz]", "S(f)", "Amplitude spectrum of seismogram", 14)
ax5.set_xlim(0, 1)
ax5.plot(f, np.absolute(spec), color='blue', ls='-', label='boxcar')

### Task 3: Acausal low pass filtering

Apply the boxcar lowpass filter to the data and plot the result.

In [ ]:
fc = 0.1
df = 1./seistrace.tlen
specfil = spec*boxcar_lowpass_filter(fc, df, spec.size)
seisfil = dft_fast_synthesis(specfil)

In [ ]:
fig6, ax6 = SetupFigure(12, 5, "Time [s]", "sf(t)", "Boxcar lowpass filtered seismic data, FC = {:5.2f} Hz".format(fc), 14)
#ax6.set_xlim(64000, 64500)
ax6.plot(t, seisfil, color='blue', ls='-')

Apply the Hann low pass filter to the data and plot the result.

In [ ]:
specfil2 = spec*hann_lowpass_filter(fc, df, spec.size)
seisfil2 = dft_fast_synthesis(specfil2)

In [ ]:
fig7, ax7 = SetupFigure(12, 5, "Time [s]", "sf(t)", "Hann lowpass filtered seismic data, FC = {:5.2f}".format(fc), 14)
#ax7.set_xlim(64000, 64500)
ax7.plot(t, seisfil2, color='blue', ls='-')

Apply the boxcar highpass filter to the data and plot the result.

In [ ]:
specfil3 = spec*boxcar_highpass_filter(fc, df, spec.size)
seisfil3 = dft_fast_synthesis(specfil3)

In [ ]:
fig8, ax8 = SetupFigure(12, 5, "Time [s]", "sf(t)", "Boxcar highpass filtered seismic data, FC = {:5.2f}".format(fc), 14)
#ax7.set_xlim(64000, 64500)
ax8.plot(t, seisfil3, color='blue', ls='-')